# Transformers ONNX

### transforemrs에서 모델들을 ONNX로 변환하기
Open Neural Network Exchange(ONNX)은 머신러닝 모델들을 built하기 위한 ecosystem, 즉 다양한 프레임워크에서 공통된 세션을 통해 실행하게 해주는 라이브러리이다.  
그런데 중요한부분이 있다. 바로 `production helps increase the speed of innovation in the AI community` 퍼포먼스를 향상시켜준다는 점이다.  
그래서 이번 장에서는 transformers에서 ONNX를 적용한 삽질기를 작성한다.




### model
tansformers에서는 각종 논문에서 언급한 bpe 같은 토크나이저와, 입력값, 레이저를 동일하게 만들어놨다.  
그래서 ONNX를 사용하기 위한 입력이 대체로 다르다.  
이 입력값이 동일하게 사용되거나 `shape_inference.infer_shapes`의 함수로 불러오고 적용만 한다면 좋으련만 아쉽게도 아직 완벽하게 적용되지 않는다.  
그래서 각 모델에 대한 ONNX 변환을 시도해본다.

프로세스는 간단하게 onnx로 변환해주고 변환해준 onnx모델을 onnx_runtime으로 세션을 열어서 사용하면 된다.

먼저 Bert는 튜토리얼에 잘 설명해줬다.  
https://github.com/huggingface/transformers/blob/master/notebooks/04-onnx-export.ipynb

In [3]:
from transformers.convert_graph_to_onnx import convert

# Handles all the above steps for you
convert(framework="pt", model="bert-base-cased", output=Path("onnx/bert-base-cased.onnx"), opset=11)

그리고 seq2seq 모델중 Conditional Generation으로 유용하게 적용할 수 있는 T5모델도 library로 잘 구현해 놓았더라.  
https://github.com/Ki6an/fastT5

이 [fastT5]는 encoder와 decoder 그리고 lm_head로 구성되는데, lm_head는 decoder가 lm_head로 init하기 때문에 필요하다. 그래서 이 3개의 모델로 나뉘어서 저장이 된다

[fastT5]: https://github.com/Ki6an/fastT5

In [4]:
from fastT5 import export_and_get_onnx_model
from transformers import AutoTokenizer

model_name = 't5-small'
model = export_and_get_onnx_model(model_name)

tokenizer = AutoTokenizer.from_pretrained(model_name)
t_input = "translate English to French: The universe is a dark forest."
token = tokenizer(t_input, return_tensors='pt')

tokens = model.generate(input_ids=token['input_ids'],
               attention_mask=token['attention_mask'],
               num_beams=2)

output = tokenizer.decode(tokens.squeeze(), skip_special_tokens=True)
print(output)

추가적으로 fastT5에도 wrap한 quantization이 있다.
onnx에서 `quantize` 함수를 이용해서 quantization을 할 수있는데, 실험 결과 1퍼센트 정도의 정확도를 떨어뜨리지만 모델의 크기를 절반에서 2/3 정도로 줄여줘서 메모리를 조금이라도 아낄 수 있다.

추가적으로(2) huggingface 4.6이상에서 돌려야 된다.  
관련이슈는 이곳 https://github.com/huggingface/transformers/pull/10651

그리고 Xlnet에서는? 입력의 encoder중 1개를 빼야되는데..... 그것은 바로